In [ ]:
import pandas as pd
import pyarrow as pa
import pyarrow.parquet as pq
import logging
import uuid
from pathlib import Path
from datetime import datetime, timedelta
from typing import Optional, Dict, List, Tuple
from client import LocalLLMClient, create_client
from news_function import analyze_news_single  # 复用单条分析函数


# --------------------------
# 1. 基础配置
# --------------------------
logging.basicConfig(
    level=logging.INFO,
    format='%(asctime)s - 批量拆分分析 - %(levelname)s - %(message)s',
    handlers=[
        logging.FileHandler("batch_split_analysis.log", encoding='utf-8'),
        logging.StreamHandler()
    ]
)
logger = logging.getLogger(__name__)

# 结果存储目录（自动创建）
OUTPUT_DIR = Path("batch_split_results")
OUTPUT_DIR.mkdir(exist_ok=True)


# --------------------------
# 2. 工具函数：写入或追加数据到Parquet文件
# --------------------------
def write_or_append_parquet(df: pd.DataFrame, file_path: str):
    """
    将DataFrame写入Parquet文件，如文件已存在则追加
    
    参数：
    - df: 要写入或追加的数据
    - file_path: 目标Parquet文件路径
    """
    table = pa.Table.from_pandas(df)
    
    # 如果文件不存在，创建新文件；否则追加
    if not Path(file_path).exists():
        pq.write_table(table, file_path)
    else:
        # 读取现有schema并追加
        existing_table = pq.read_table(file_path)
        with pq.ParquetWriter(file_path, existing_table.schema) as writer:
            writer.write_table(table)


# --------------------------
# 3. 核心函数：生成双表数据（单日结果）
# --------------------------
def _process_daily_results(daily_results: List[Dict]) -> Tuple[pd.DataFrame, pd.DataFrame]:
    """处理单日结果，生成行业裁决表和个股推荐表的DataFrame"""
    industry_records: List[Dict] = []
    stock_records: List[Dict] = []

    for result in daily_results:
        # 基础元数据
        base_meta = {
            "original_news_id": result["original_news_id"],
            "original_news_date": result["original_news_date"],
            "original_news_title": result["original_news_title"],
            "analysis_status": result["status"],
            "error_msg": result["error_msg"],
            "log_path": result["log_path"],
            "analysis_time": result["analysis_batch_time"]
        }

        # 处理分析失败的记录
        if result["status"] == "failed":
            industry_records.append({
                **base_meta,
                "analysis_id": f"ana_{uuid.uuid4().hex[:8]}",
                "industry": "",
                "impact_direction": "",
                "confidence_score": 0,
                "comprehensive_reason": ""
            })
            continue

        # 处理分析成功的记录
        for industry in result["ruled_industries"]:
            current_analysis_id = f"ana_{uuid.uuid4().hex[:8]}"

            # 行业裁决主表记录
            industry_records.append({
                **base_meta,
                "analysis_id": current_analysis_id,
                "industry": industry.get("industry", ""),
                "impact_direction": industry.get("impact", ""),
                "confidence_score": industry.get("confidence", 0),
                "comprehensive_reason": industry.get("comprehensive_reason", "")
            })

            # 个股推荐副表记录
            for rank, stock in enumerate(industry.get("stocks", []), 1):
                stock_records.append({
                    "analysis_id": current_analysis_id,
                    "stock_name": stock.get("name", ""),
                    "stock_code": stock.get("code", ""),
                    "recommendation_reason": stock.get("reason", ""),
                    "stock_rank": rank
                })

    # 转换为DataFrame并调整字段顺序
    industry_df = pd.DataFrame(industry_records)[[
        "analysis_id", "original_news_id", "original_news_date", "original_news_title",
        "industry", "impact_direction", "confidence_score", "comprehensive_reason",
        "analysis_status", "error_msg", "log_path", "analysis_time"
    ]]

    stock_df = pd.DataFrame(stock_records)[[
        "analysis_id", "stock_name", "stock_code", "recommendation_reason", "stock_rank"
    ]]

    return industry_df, stock_df


# --------------------------
# 4. 批量分析主函数（按日期保存）
# --------------------------
def batch_analyze_split_parquet(
    input_parquet: str,
    news_date: str,
    debate_rounds: int = 2,
    llm_client: Optional[LocalLLMClient] = None,** llm_kwargs
) -> Tuple[str, str]:
    """
    批量分析Parquet新闻，按日期完成后统一保存结果
    
    参数：
    - input_parquet: 输入新闻Parquet路径
    - news_date: 新闻日期
    - debate_rounds: 辩论轮次
    - llm_client: 已实例化的LLM客户端
    - **llm_kwargs: 创建LLM客户端的参数
    
    返回：
    - 行业裁决表路径, 个股推荐表路径
    """
    # 1. 初始化LLM客户端
    if not llm_client:
        try:
            llm_client = create_client(** llm_kwargs)
            logger.info("LLM客户端初始化成功")
        except Exception as e:
            raise Exception(f"LLM客户端初始化失败：{str(e)}")

    # 2. 读取并处理输入Parquet
    try:
        logger.info(f"读取输入Parquet：{input_parquet}")
        input_df = pd.read_parquet(input_parquet)
        required_cols = ["id", "date", "title", "content"]
        missing_cols = [col for col in required_cols if col not in input_df.columns]
        if missing_cols:
            raise Exception(f"输入缺少字段：{', '.join(missing_cols)}")
        
        # 筛选出指定日期的新闻并排序
        input_df_filtered = input_df[input_df["date"] == news_date].sort_values(by="id", ascending=True).reset_index(drop=True)
        total_news = len(input_df_filtered)
        logger.info(f"读取 {total_news} 条 {news_date} 的新闻")
    except Exception as e:
        raise Exception(f"读取输入失败：{str(e)}")

    # 如果当天没有新闻，直接返回空路径
    if total_news == 0:
        logger.info(f"{news_date} 没有新闻需要分析")
        return "", ""

    # 3. 准备输出文件路径（带日期标识）
    date_suffix = news_date.replace("-", "")
    industry_path = OUTPUT_DIR / f"industry_verdict_{date_suffix}.parquet"
    stock_path = OUTPUT_DIR / f"stock_recommendation_{date_suffix}.parquet"
    
    # 4. 处理当日所有新闻
    daily_results: List[Dict] = []
    processed_count = 0

    for idx, row in input_df_filtered.iterrows():
        news_id = str(row["id"])
        logger.info(f"分析第 {idx+1}/{total_news} 条新闻（ID：{news_id}）")
        
        # 调用单条分析函数
        single_result = analyze_news_single(
            news_title=str(row["title"]),
            news_content=str(row["content"]),
            debate_rounds=debate_rounds,
            llm_client=llm_client
        )

        # 补充原始新闻元数据
        single_result.update({
            "original_news_id": news_id,
            "original_news_date": str(row["date"]),
            "original_news_title": str(row["title"]),
            "analysis_batch_time": datetime.now().strftime("%Y-%m-%d %H:%M:%S")
        })
        daily_results.append(single_result)
        processed_count += 1

    # 5. 当日新闻分析完成后，统一保存结果
    logger.info(f"{news_date} 新闻分析完成，共处理 {processed_count} 条，开始保存结果...")
    
    # 处理当日结果
    daily_industry_df, daily_stock_df = _process_daily_results(daily_results)
    
    # 保存结果（如文件已存在则追加）
    write_or_append_parquet(daily_industry_df, str(industry_path))
    write_or_append_parquet(daily_stock_df, str(stock_path))
    
    logger.info(f"{news_date} 结果保存完成，行业裁决表：{industry_path}，个股推荐表：{stock_path}")

    return str(industry_path), str(stock_path)


# --------------------------
# 5. 使用示例
# --------------------------
if __name__ == "__main__":
    # 配置参数
    INPUT_PARQUET = "../data/stock_daily_cctvnews.parquet"  # 输入新闻路径
    DEBATE_ROUNDS = 2  # 辩论轮次
    LLM_KWARGS = {
        # "model": "gpt-4-turbo",  # 实际使用时填写LLM参数
        # "api_key": "your_api_key"
    }

    # 获取20250101至今以来的日期列表，形成yyyy-mm-dd的格式
    start_date = datetime(2025, 4, 4)
    end_date = datetime.now()
    date_list = [start_date + timedelta(days=x) for x in range((end_date - start_date).days + 1)]
    date_list = [date.strftime("%Y-%m-%d") for date in date_list]

    # 依次遍历date_list ，对每个日期进行分析
    for news_date in date_list:
        try:
            # 执行批量拆分分析
            industry_table_path, stock_table_path = batch_analyze_split_parquet(
                input_parquet=INPUT_PARQUET,
                news_date=news_date,
                debate_rounds=DEBATE_ROUNDS,** LLM_KWARGS
            )
            
            if industry_table_path and stock_table_path:
                # 打印结果
                print("="*70)
                print(f"{news_date} 分析完成！")
                print(f"输入文件：{INPUT_PARQUET}")
                print(f"行业裁决表：{industry_table_path}")
                print(f"个股推荐表：{stock_table_path}")
                print(f"提示：可通过 'analysis_id' 字段关联两张表")
                print("="*70)
        except Exception as e:
            print(f"{news_date} 分析失败：{str(e)}")
            logger.error(f"{news_date} 分析失败：{str(e)}")


2025-10-13 10:39:25,015 - INFO - LLM客户端初始化成功
2025-10-13 10:39:25,016 - INFO - 读取输入Parquet：../data/stock_daily_cctvnews.parquet
2025-10-13 10:39:25,045 - INFO - 读取 14 条 2025-04-04 的新闻
2025-10-13 10:39:25,046 - INFO - 分析第 1/14 条新闻（ID：115575）
2025-10-13 10:39:25,047 - INFO - 开始分析单条新闻（ID：news_single_20251013103925_778，标题：汇聚共建美丽中国磅礴力量——习近平总书记参加首都义务植树活动...）
2025-10-13 10:39:25,048 - INFO - 请求模型: qwen3:30b-a3b-instruct-2507-q4_K_M
2025-10-13 10:39:25,049 - INFO - 用户消息: 标题：汇聚共建美丽中国磅礴力量——习近平总书记参加首都义务植树活动时的重要讲话在广大干部群众中引发热烈反响
内容：央视网消息
（新闻联播）：习近平总书记在参加首都义务植树活动时强调，植树造林是生态文明建设重要一环。各地区各部门要进一步行动起来，动员组织广大干部群众积极参与造林绿化，汇聚共建美丽中国的磅礴力量。总书记的重要讲话在各地引发热烈反响，大家表示，要践行绿色发展理念，弘扬生态文化，让祖国大地更加绿意盎然、生机勃发。
4月3日，习近平总书记来到北京市丰台区永定河畔，同干部群众一起参加义务植树。党的十八大以来，习近平总书记已连续13年参加首都义务植树活动。
在习近平生态文明思想指引下，我国生态环境保护发生历史性、转折性、全局性变化。习近平总书记指出，目前我国森林覆盖率已经超过25%，贡献了约25%的全球新增绿化面积。经过持续努力，塔克拉玛干沙漠戴上了“绿围脖”，科尔沁沙地正重现草原风光，成绩来之不易。总书记的重要讲话激励广大干部群众积极造林绿化、共建美丽中国。
习近平总书记指出，绿化祖国必须坚持扩绿兴绿护绿“三绿”并举，推动森林水库、钱库、粮库、碳库“四库”联动，为科学推进国土绿化、建设美丽中国指明方向。
增绿就是增优势，植树就是植未来。广大干部群

2025-04-04 分析完成！
输入文件：../data/stock_daily_cctvnews.parquet
行业裁决表：batch_split_results\industry_verdict_20250404.parquet
个股推荐表：batch_split_results\stock_recommendation_20250404.parquet
提示：可通过 'analysis_id' 字段关联两张表


2025-10-13 10:46:53,377 - INFO - 读取 13 条 2025-04-05 的新闻
2025-10-13 10:46:53,378 - INFO - 分析第 1/13 条新闻（ID：115589）
2025-10-13 10:46:53,379 - INFO - 开始分析单条新闻（ID：news_single_20251013104653_982，标题：【新思想引领新征程】传承伟大精神 凝聚民族力量...）
2025-10-13 10:46:53,380 - INFO - 请求模型: qwen3:30b-a3b-instruct-2507-q4_K_M
2025-10-13 10:46:53,381 - INFO - 用户消息: 标题：【新思想引领新征程】传承伟大精神 凝聚民族力量
内容：央视网消息
（新闻联播）：天地英雄气，千秋尚凛然。习近平总书记强调：“理想之光不灭，信念之光不灭。我们一定要铭记烈士们的遗愿，永志不忘他们为之流血牺牲的伟大理想。”清明时节，各地以多种形式缅怀英烈，寄托哀思，厚植家国情怀，汲取新时代奋进力量。 

又是一年清明时，追思先烈祭英魂。

从东北抗联的密林到西南边陲的哨所，从湖北红安革命烈士纪念设施到辽宁沈阳抗美援朝烈士陵园，人们在致敬英烈中传承红色基因，在抚今追昔中坚定前行意志。

铭记历史、缅怀英烈一直是习近平总书记情之所牵、行之所至。党的十八大以来，习近平总书记以上率下、躬亲垂范，从吕梁山到大别山，从云贵高原到西北大漠，总书记缅怀英烈的足迹遍布祖国大江南北。每一次深情的凝望都寄托了他对革命先烈和人民英雄的深切缅怀与致敬。

在习近平总书记引领推动下，我国以立法形式设立烈士纪念日、中国人民抗日战争胜利纪念日和南京大屠杀死难者国家公祭日，出台英雄烈士保护法等一系列法律法规，建立起“共和国勋章”“七一勋章”“八一勋章”等中国特色功勋荣誉表彰制度体系。

崇尚英雄、争做英雄，在全社会已蔚然成风。

崇尚英雄才会产生英雄，争做英雄才能英雄辈出。在英烈们为之奋斗的祖国大地上，一代代的后来者扛起前人肩上的责任。

在广西百色乐业县百坭村，“七一勋章”获得者黄文秀烈士奋斗过的热土，一批批返乡青年接力奋斗，投入乡村振兴，青春力量正描绘着“民富村强景美”的新图景。

在黄大年教授工作过的吉林大学，师生们赓续“心有大我 至诚报

2025-04-05 分析完成！
输入文件：../data/stock_daily_cctvnews.parquet
行业裁决表：batch_split_results\industry_verdict_20250405.parquet
个股推荐表：batch_split_results\stock_recommendation_20250405.parquet
提示：可通过 'analysis_id' 字段关联两张表


2025-10-13 10:53:35,729 - INFO - 响应内容: {"positive": []}...
2025-10-13 10:53:35,730 - INFO - 响应时间: 1558.17毫秒
2025-10-13 10:53:35,731 - INFO - 请求模型: qwen3:30b-a3b-instruct-2507-q4_K_M
2025-10-13 10:53:35,731 - INFO - 用户消息: 正方首次观点：{"positive": []}
新闻内容：标题：《习近平关于中国式现代化论述摘编》西班牙文版出版发行
内容：央视网消息
（新闻联播）：中共中央党史和文献研究院翻译的《习近平关于中国式现代化论述摘编》一书西班牙文版，近日由中央编译出版社出版，面向海内外发行。

《习近平关于中国式现代化论述摘编》由中共中央党史和文献研究院编辑，收录了习近平同志围绕中国式现代化发表的一系列重要论述。该书西班牙文版和此前出版的英文、法文、俄文、阿文、日文版，对于国外读者深刻理解中国式现代化的理论体系和实践要求，深入了解中国共产党团结带领中国人民成功走出的中国式现代化新道路、创造的人类文明新形态、展现的现代化新图景，增强国际社会携手同行现代化之路，实现和平发展、互利合作、共同繁荣的世界现代化的共同认识，具有重要意义。
请针对正方观点进行驳斥并提出利空
2025-10-13 10:53:35,732 - INFO - 参数: {'temperature': 0.4, 'max_tokens': 20000}
2025-10-13 10:53:37,902 - INFO - 响应内容: {"negative": [], "refute": "该新闻为政策宣介，不直接刺激具体行业，难以形成可交易的实质性利好，机构普遍认为其情绪驱动有限，难支撑股价持续上涨。"}...
2025-10-13 10:53:37,902 - INFO - 响应时间: 2171.44毫秒
2025-10-13 10:53:37,903 - INFO - 请求模型: qwen3:30b-a3b-instruct-2507-q4_K_M
2025-10-13 10:53:37,904 - INFO - 用户消息: 之前的辩论内容：{"pro_initial": {"positi

...

2025-10-13 12:49:43,910 - ERROR - 请求失败: API请求失败: ('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))
2025-10-13 12:49:43,912 - ERROR - 单条新闻分析失败：正方初始观点失败：LLM调用失败（3次重试）：LLM调用失败：API请求失败: ('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))
2025-10-13 12:49:43,914 - INFO - 分析第 2/14 条新闻（ID：116386）
2025-10-13 12:49:43,914 - INFO - 开始分析单条新闻（ID：news_single_20251013124943_772，标题：龙舟竞渡 粽叶飘香 各地共度端午...）
2025-10-13 12:49:43,915 - INFO - 请求模型: qwen3:30b-a3b-instruct-2507-q4_K_M
2025-10-13 12:49:43,916 - INFO - 用户消息: 标题：龙舟竞渡 粽叶飘香 各地共度端午
内容：央视网消息
（新闻联播）：端午佳节，人们划龙舟、包粽子、做香囊、参观红色景区……用多种方式，追思爱国先贤、赓续传统文化、涵养家国情怀。
浪花飞溅，龙舟飞驰。在湖南岳阳汨罗江沿线，当地的民间龙舟队齐聚汨罗江上，展开激烈角逐；在“屈原故里”湖北秭归，龙舟队员们以鼓点为令，齐心协力，奋勇争先。千百年来，人们用这样的方式致敬屈原的爱国精神。
连日来，从南海之滨到白山黑水，人们逐浪竞桨，共同感受中华传统文化的魅力。在海南三沙永兴岛，渔民们将渔船装扮成“渔家龙舟”；在广东深圳，来自大湾区的29支龙舟队伍，在碧波万顷的海面上展开了一场力量与速度的对决；在北京通州的大运河上、黑龙江哈尔滨的松花江上、吉林大安的嫩江上人们劈波斩浪；在安徽望江莲花湖、江苏苏州金鸡湖上，大家奋楫拼搏，赢得岸边观众阵阵呐喊。
端午时节，粽叶飘香。在广西玉林容县，大家围坐在庭院中包起长条粽、牛角粽等特色粽子；在

2025-05-31 分析失败："None of [Index(['analysis_id', 'stock_name', 'stock_code', 'recommendation_reason',\n       'stock_rank'],\n      dtype='object')] are in the [columns]"


2025-10-13 12:49:46,734 - ERROR - 单条新闻分析失败：正方初始观点失败：LLM调用失败（3次重试）：LLM调用失败：API请求失败: ('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))
2025-10-13 12:49:46,736 - INFO - 分析第 2/14 条新闻（ID：116400）
2025-10-13 12:49:46,737 - INFO - 开始分析单条新闻（ID：news_single_20251013124946_188，标题：【新思想引领新征程】筑梦童心 托起明天的太阳...）
2025-10-13 12:49:46,739 - INFO - 请求模型: qwen3:30b-a3b-instruct-2507-q4_K_M
2025-10-13 12:49:46,739 - INFO - 用户消息: 标题：【新思想引领新征程】筑梦童心 托起明天的太阳
内容：央视网消息
（新闻联播）：少年儿童是祖国的未来，是中华民族的希望。习近平总书记始终高度重视少年儿童健康成长，指出：“新时代中国儿童应该是有志向、有梦想，爱学习、爱劳动，懂感恩、懂友善，敢创新、敢奋斗，德智体美劳全面发展的好儿童。”谆谆教导，语重心长，新时代少年儿童在总书记的关心关怀下，向阳生长，逐梦前行，努力成长为能够担当民族复兴大任的时代新人。
“六一”前夕，习近平总书记向中国少年先锋队第九次全国代表大会致贺信，在信中总书记祝全国的小朋友们节日快乐。每到“六一”，这份祝福总会如约而至，让孩子们倍感温暖和激励。
从节日的谆谆寄语，到考察调研时的真挚关爱，再到尺素传情的殷切期望，习近平总书记始终对少年儿童悉心关怀、寄予期待。
从“要长得壮壮的、练得棒棒的”“让孩子们跑起来”，到“提高学生审美和人文素养”，再到“从小培养劳动意识、环保意识、节约意识”，小朋友们的点滴成长，习近平总书记始终放在心上，反复叮嘱、悉心嘱托，为少年儿童身心健康、全面发展护航，为中国未来“培土筑基”。
言之殷殷，情之切切。在习爷爷的鼓励下，一个个小小的梦想正在开花、结果。去年，北京市八一学校的沈跃然和小伙伴们成功获得国际青少年无人系统竞技挑战赛水下项目大

2025-06-01 分析完成！
输入文件：../data/stock_daily_cctvnews.parquet
行业裁决表：batch_split_results\industry_verdict_20250601.parquet
个股推荐表：batch_split_results\stock_recommendation_20250601.parquet
提示：可通过 'analysis_id' 字段关联两张表


2025-10-13 12:51:29,429 - INFO - 响应内容: {"positive": [{"industry":"综合环境治理","reason":"生态文明建设持续推进，山水林田湖草沙一体化治理加速，带动环境治理工程需求上升。","stocks":[{"name":"碧水源","code":"300070","reason":"专注水环境治理，受益于太湖、湖泊等重点水域治理工程。"},{"name":"中环环保","code":"300692","rea...
2025-10-13 12:51:29,430 - INFO - 响应时间: 6450.58毫秒
2025-10-13 12:51:29,431 - INFO - 请求模型: qwen3:30b-a3b-instruct-2507-q4_K_M
2025-10-13 12:51:29,432 - INFO - 用户消息: 正方首次观点：{"positive": [{"industry": "综合环境治理", "reason": "生态文明建设持续推进，山水林田湖草沙一体化治理加速，带动环境治理工程需求上升。", "stocks": [{"name": "碧水源", "code": "300070", "reason": "专注水环境治理，受益于太湖、湖泊等重点水域治理工程。"}, {"name": "中环环保", "code": "300692", "reason": "主营污水处理与环境修复，深度参与多地生态治理项目。"}]}, {"industry": "园林工程", "reason": "生态文明建设推动国土绿化与生态修复，植树造林、林冠下造林等项目密集落地。", "stocks": [{"name": "铁汉生态", "code": "300197", "reason": "深耕生态修复与园林工程，受益于塞罕坝、大兴安岭等绿化项目。"}, {"name": "蒙草生态", "code": "300355", "reason": "专注生态修复与草原治理，受益于荒漠化防治与生态修复政策。"}]}, {"industry": "固废治理", "reason": "生态清淤、淤泥上岸处理等工程推动固废治理需求增长，太湖等重点区域治理项目密集启动。", "stocks": [{"name"